# Analysis_for_FITB_part2
- We will do .....
- Then we will do

# Table of Content
## Step4: Preprocessing
4.1) Import necessary packages  
4.2) Load data from hard disk 
4.3) Prepare train and test sets
4.4) Explore different models

## Step5: Modeling

# Step4: Preprocessing
Ignore 4.4) (we just do some exploration)

## 4.1) Import necessary packages

In [1]:
# Import packages
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.model_selection import TimeSeriesSplit, cross_validate
from sklearn.model_selection import (GridSearchCV, cross_val_score)

from sklearn.linear_model import (LinearRegression, Ridge)
from sklearn.ensemble import (RandomForestRegressor, GradientBoostingRegressor)
from sklearn.dummy import DummyRegressor
from sklearn.neighbors import KNeighborsRegressor

from sklearn.metrics import mean_squared_error,  r2_score, mean_absolute_error

from sklearn.pipeline import make_pipeline

from sklearn.preprocessing import StandardScaler

from sklearn.feature_selection import SelectKBest, f_regression

import statsmodels.api as sm
from statsmodels.tsa.arima.model import ARIMA

import time


## 4.2) Load data from hard disk

In [2]:
# Read data back after restart computer.
fitb_1 = pd.read_csv('../data/fitb_1.csv',
                 header=0,
                 parse_dates=['Date'],
                 index_col=0,
                 infer_datetime_format= True)
# Now we will have index as DatetimeIndex

fitb_1.head()

Open   High    Low  Close     Volume  Ex-Dividend  Split Ratio  \
Date                                                                          
2000-01-03  72.75  72.75  68.69  69.87   980800.0          0.0          1.0   
2000-01-04  68.31  68.50  65.88  66.94  1047400.0          0.0          1.0   
2000-01-05  67.13  67.44  65.50  66.44   745667.0          0.0          1.0   
2000-01-06  66.00  68.31  65.00  68.25  1189667.0          0.0          1.0   
2000-01-07  68.00  69.00  66.81  67.81   565800.0          0.0          1.0   

            Adj. Open  Adj. High   Adj. Low  ...  log_rtn_lag_11  \
Date                                         ...                   
2000-01-03  30.954975  30.954975  29.227453  ...             NaN   
2000-01-04  29.065764  29.146609  28.031804  ...             NaN   
2000-01-05  28.563677  28.695581  27.870115  ...             NaN   
2000-01-06  28.082864  29.065764  27.657366  ...             NaN   
2000-01-07  28.933860  29.359358  28.427517  ...             NaN   

            log_rtn_lag_12  log_rtn_lag_13  log_rtn_lag_14  month  month_sin  \
Date                                                                           
2000-01-03             NaN             NaN             NaN      1        0.5   
2000-01-04             NaN             NaN             NaN      1        0.5   
2000-01-05             NaN             NaN             NaN      1        0.5   
2000-01-06             NaN             NaN             NaN      1        0.5   
2000-01-07             NaN             NaN             NaN      1        0.5   

            month_cos  1d_future_month  1d_future_month_sin  \
Date                                                          
2000-01-03   0.866025              1.0                  0.5   
2000-01-04   0.866025              1.0                  0.5   
2000-01-05   0.866025              1.0                  0.5   
2000-01-06   0.866025              1.0                  0.5   
2000-01-07   0.866025              1.0                  0.5   

            1d_future_month_cos  
Date                             
2000-01-03             0.866025  
2000-01-04             0.866025  
2000-01-05             0.866025  
2000-01-06             0.866025  
2000-01-07             0.866025  

[5 rows x 43 columns]

In [3]:
fitb_1.tail()

Open    High      Low  Close     Volume  Ex-Dividend  \
Date                                                                
2018-03-21  33.49  33.975  33.2825  33.62  4176448.0          0.0   
2018-03-22  33.21  33.330  32.2700  32.30  6857624.0          0.0   
2018-03-23  32.44  32.540  31.0000  31.03  6691187.0          0.0   
2018-03-26  31.59  32.185  31.2600  32.12  4890979.0          0.0   
2018-03-27  32.33  32.430  31.0650  31.34  4642002.0          0.0   

            Split Ratio  Adj. Open  Adj. High  Adj. Low  ...  log_rtn_lag_11  \
Date                                                     ...                   
2018-03-21          1.0      33.49     33.975   33.2825  ...        0.008953   
2018-03-22          1.0      33.21     33.330   32.2700  ...        0.000594   
2018-03-23          1.0      32.44     32.540   31.0000  ...       -0.000297   
2018-03-26          1.0      31.59     32.185   31.2600  ...        0.015911   
2018-03-27          1.0      32.33     32.430   31.0650  ...        0.001460   

            log_rtn_lag_12  log_rtn_lag_13  log_rtn_lag_14  month  month_sin  \
Date                                                                           
2018-03-21        0.013581        0.003653       -0.007898      3        1.0   
2018-03-22        0.008953        0.013581        0.003653      3        1.0   
2018-03-23        0.000594        0.008953        0.013581      3        1.0   
2018-03-26       -0.000297        0.000594        0.008953      3        1.0   
2018-03-27        0.015911       -0.000297        0.000594      3        1.0   

               month_cos  1d_future_month  1d_future_month_sin  \
Date                                                             
2018-03-21  6.123234e-17              3.0                  1.0   
2018-03-22  6.123234e-17              3.0                  1.0   
2018-03-23  6.123234e-17              3.0                  1.0   
2018-03-26  6.123234e-17              3.0                  1.0   
2018-03-27  6.123234e-17              NaN                  NaN   

            1d_future_month_cos  
Date                             
2018-03-21         6.123234e-17  
2018-03-22         6.123234e-17  
2018-03-23         6.123234e-17  
2018-03-26         6.123234e-17  
2018-03-27                  NaN  

[5 rows x 43 columns]

In [4]:
fitb_1.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 4586 entries, 2000-01-03 to 2018-03-27
Data columns (total 43 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   Open                 4586 non-null   float64
 1   High                 4586 non-null   float64
 2   Low                  4586 non-null   float64
 3   Close                4586 non-null   float64
 4   Volume               4586 non-null   float64
 5   Ex-Dividend          4586 non-null   float64
 6   Split Ratio          4586 non-null   float64
 7   Adj. Open            4586 non-null   float64
 8   Adj. High            4586 non-null   float64
 9   Adj. Low             4586 non-null   float64
 10  Adj. Close           4586 non-null   float64
 11  Adj. Volume          4586 non-null   float64
 12  log_rtn              4585 non-null   float64
 13  ma14                 4573 non-null   float64
 14  rsi14                4572 non-null   float64
 15  ma50                

In [5]:
fitb_1.index

DatetimeIndex(['2000-01-03', '2000-01-04', '2000-01-05', '2000-01-06',
               '2000-01-07', '2000-01-10', '2000-01-11', '2000-01-12',
               '2000-01-13', '2000-01-14',
               ...
               '2018-03-14', '2018-03-15', '2018-03-16', '2018-03-19',
               '2018-03-20', '2018-03-21', '2018-03-22', '2018-03-23',
               '2018-03-26', '2018-03-27'],
              dtype='datetime64[ns]', name='Date', length=4586, freq=None)

In [6]:
fitb_1.describe().T

count          mean           std            min  \
Open                 4586.0  3.176914e+01  1.846588e+01       1.050000   
High                 4586.0  3.215708e+01  1.865661e+01       1.350000   
Low                  4586.0  3.136244e+01  1.826728e+01       1.010000   
Close                4586.0  3.177690e+01  1.848722e+01       1.030000   
Volume               4586.0  7.757590e+06  9.684681e+06  268500.000000   
Ex-Dividend          4586.0  3.085478e-03  2.929205e-02       0.000000   
Split Ratio          4586.0  1.000109e+00  7.383342e-03       1.000000   
Adj. Open            4586.0  2.356285e+01  1.080905e+01       0.878177   
Adj. High            4586.0  2.384678e+01  1.088750e+01       1.129085   
Adj. Low             4586.0  2.326631e+01  1.073052e+01       0.844723   
Adj. Close           4586.0  2.356719e+01  1.082226e+01       0.861450   
Adj. Volume          4586.0  7.771788e+06  9.675486e+06  268500.000000   
log_rtn              4585.0  1.150579e-05  3.275979e-02      -0.573166   
ma14                 4573.0  2.354744e+01  1.081050e+01       1.311292   
rsi14                4572.0  5.117968e+01  1.119603e+01      12.646920   
ma50                 4537.0  2.349994e+01  1.079349e+01       1.757685   
rsi50                4536.0  5.087071e+01  5.753122e+00      31.464905   
ma200                4387.0  2.334013e+01  1.077220e+01       5.049642   
rsi200               4386.0  5.032658e+01  3.078050e+00      40.803345   
vol_1d_change        4585.0  2.506145e-04  3.938113e-01      -1.977245   
vol_1d_change_ma10   4576.0  2.950112e-04  5.378792e-02      -0.265976   
1d_future_log_rtn    4585.0  1.150579e-05  3.275979e-02      -0.573166   
log_rtn_lag_0        4585.0  1.150579e-05  3.275979e-02      -0.573166   
log_rtn_lag_1        4584.0  1.687122e-05  3.276134e-02      -0.573166   
log_rtn_lag_2        4583.0  9.341758e-06  3.276095e-02      -0.573166   
log_rtn_lag_3        4582.0  1.809822e-05  3.275916e-02      -0.573166   
log_rtn_lag_4        4581.0  2.684565e-05  3.275739e-02      -0.573166   
log_rtn_lag_5        4580.0  2.626624e-05  3.276094e-02      -0.573166   
log_rtn_lag_6        4579.0  2.685738e-05  3.276449e-02      -0.573166   
log_rtn_lag_7        4578.0  2.751200e-05  3.276804e-02      -0.573166   
log_rtn_lag_8        4577.0  2.654394e-05  3.277156e-02      -0.573166   
log_rtn_lag_9        4576.0  2.687498e-05  3.277513e-02      -0.573166   
log_rtn_lag_10       4575.0  2.972295e-05  3.277815e-02      -0.573166   
log_rtn_lag_11       4574.0  3.100947e-05  3.278162e-02      -0.573166   
log_rtn_lag_12       4573.0  3.069687e-05  3.278519e-02      -0.573166   
log_rtn_lag_13       4572.0  2.722354e-05  3.278794e-02      -0.573166   
log_rtn_lag_14       4571.0  2.729446e-05  3.279153e-02      -0.573166   
month                4586.0  6.483428e+00  3.444314e+00       1.000000   
month_sin            4586.0  1.673016e-03  7.088761e-01      -1.000000   
month_cos            4586.0 -3.989147e-03  7.054743e-01      -1.000000   
1d_future_month      4585.0  6.484624e+00  3.443738e+00       1.000000   
1d_future_month_sin  4585.0  1.564329e-03  7.089152e-01      -1.000000   
1d_future_month_cos  4585.0 -4.178899e-03  7.054342e-01      -1.000000   

                              25%           50%           75%           max  
Open                 1.556000e+01  2.546500e+01  4.874500e+01  7.275000e+01  
High                 1.578000e+01  2.575050e+01  4.939500e+01  7.275000e+01  
Low                  1.536250e+01  2.508000e+01  4.819000e+01  7.075000e+01  
Close                1.557625e+01  2.541500e+01  4.877000e+01  7.156000e+01  
Volume               2.079200e+06  5.235950e+06  9.882025e+06  1.985302e+08  
Ex-Dividend          0.000000e+00  0.000000e+00  0.000000e+00  4.400000e-01  
Split Ratio          1.000000e+00  1.000000e+00  1.000000e+00  1.500000e+00  
Adj. Open            1.382104e+01  2.338103e+01  3.231323e+01  4.579200e+01  
Adj. High            1.397523e+01  2.378372e+01  3.262088e+01  

## 4.3) Prepare train and test sets

In [7]:
fitb_1.columns

Index(['Open', 'High', 'Low', 'Close', 'Volume', 'Ex-Dividend', 'Split Ratio',
       'Adj. Open', 'Adj. High', 'Adj. Low', 'Adj. Close', 'Adj. Volume',
       'log_rtn', 'ma14', 'rsi14', 'ma50', 'rsi50', 'ma200', 'rsi200',
       'vol_1d_change', 'vol_1d_change_ma10', '1d_future_log_rtn',
       'log_rtn_lag_0', 'log_rtn_lag_1', 'log_rtn_lag_2', 'log_rtn_lag_3',
       'log_rtn_lag_4', 'log_rtn_lag_5', 'log_rtn_lag_6', 'log_rtn_lag_7',
       'log_rtn_lag_8', 'log_rtn_lag_9', 'log_rtn_lag_10', 'log_rtn_lag_11',
       'log_rtn_lag_12', 'log_rtn_lag_13', 'log_rtn_lag_14', 'month',
       'month_sin', 'month_cos', '1d_future_month', '1d_future_month_sin',
       '1d_future_month_cos'],
      dtype='object')

In [8]:
col_list = ['ma50', 'rsi50', 'vol_1d_change', 'vol_1d_change_ma10',
       'log_rtn_lag_0', 'log_rtn_lag_1', 'log_rtn_lag_2', 'log_rtn_lag_3',
       'log_rtn_lag_4', 'log_rtn_lag_5', 'log_rtn_lag_6', 'log_rtn_lag_7',
       'log_rtn_lag_8', 'log_rtn_lag_9', 'log_rtn_lag_10', 'log_rtn_lag_11',
       'log_rtn_lag_12', 'log_rtn_lag_13', 'log_rtn_lag_14']

In [9]:
# Take X_train and y_train 
X_train = fitb_1.loc["2012":"2017", col_list].copy()
y_train = fitb_1.loc["2012":"2017", '1d_future_log_rtn'].copy()
print(X_train.shape, y_train.shape)

(1508, 19) (1508,)


In [10]:
# Take X_test and y_test 
X_test = fitb_1.loc["2018-01-02":"2018-02-06", col_list].copy()
y_test = fitb_1.loc["2018-01-02":"2018-02-06", '1d_future_log_rtn'].copy()
print(X_test.shape, y_test.shape)

(25, 19) (25,)


In [11]:
X_train.index

DatetimeIndex(['2012-01-03', '2012-01-04', '2012-01-05', '2012-01-06',
               '2012-01-09', '2012-01-10', '2012-01-11', '2012-01-12',
               '2012-01-13', '2012-01-17',
               ...
               '2017-12-15', '2017-12-18', '2017-12-19', '2017-12-20',
               '2017-12-21', '2017-12-22', '2017-12-26', '2017-12-27',
               '2017-12-28', '2017-12-29'],
              dtype='datetime64[ns]', name='Date', length=1508, freq=None)

In [12]:
X_train.head()

ma50      rsi50  vol_1d_change  vol_1d_change_ma10  \
Date                                                                  
2012-01-03  10.377298  54.961759       0.817082           -0.003241   
2012-01-04  10.403321  54.994344      -0.481375            0.013092   
2012-01-05  10.429901  56.222464       0.556166            0.012964   
2012-01-06  10.462329  56.286527      -0.050195            0.051331   
2012-01-09  10.488130  55.973096      -0.041159            0.012241   

            log_rtn_lag_0  log_rtn_lag_1  log_rtn_lag_2  log_rtn_lag_3  \
Date                                                                     
2012-01-03       0.027909      -0.014827       0.026291      -0.007479   
2012-01-04       0.000764       0.027909      -0.014827       0.026291   
2012-01-05       0.028616       0.000764       0.027909      -0.014827   
2012-01-06       0.001484       0.028616       0.000764       0.027909   
2012-01-09      -0.005575       0.001484       0.028616       0.000764   

            log_rtn_lag_4  log_rtn_lag_5  log_rtn_lag_6  log_rtn_lag_7  \
Date                                                                     
2012-01-03      -0.007034      -0.005824       0.033461       0.024312   
2012-01-04      -0.007479      -0.007034      -0.005824       0.033461   
2012-01-05       0.026291      -0.007479      -0.007034      -0.005824   
2012-01-06      -0.014827       0.026291      -0.007479      -0.007034   
2012-01-09       0.027909      -0.014827       0.026291      -0.007479   

            log_rtn_lag_8  log_rtn_lag_9  log_rtn_lag_10  log_rtn_lag_11  \
Date                                                                       
2012-01-03       0.029132      -0.019239        0.008320        0.014304   
2012-01-04       0.024312       0.029132       -0.019239        0.008320   
2012-01-05       0.033461       0.024312        0.029132       -0.019239   
2012-01-06      -0.005824       0.033461        0.024312        0.029132   
2012-01-09      -0.007034      -0.005824        0.033461        0.024312   

            log_rtn_lag_12  log_rtn_lag_13  log_rtn_lag_14  
Date                                                        
2012-01-03       -0.009279       -0.026514       -0.022636  
2012-01-04        0.014304       -0.009279       -0.026514  
2012-01-05        0.008320        0.014304       -0.009279  
2012-01-06       -0.019239        0.008320        0.014304  
2012-01-09        0.029132       -0.019239        0.008320

In [13]:
y_train.head()

Date
2012-01-03    0.000764
2012-01-04    0.028616
2012-01-05    0.001484
2012-01-06   -0.005575
2012-01-09    0.031912
Name: 1d_future_log_rtn, dtype: float64

In [14]:
X_train.tail()

ma50      rsi50  vol_1d_change  vol_1d_change_ma10  \
Date                                                                
2017-12-22  29.2411  59.868957      -0.497860           -0.135801   
2017-12-26  29.2917  59.128890      -0.285393           -0.090914   
2017-12-27  29.3437  59.035808       0.126103           -0.106589   
2017-12-28  29.3891  58.941127       0.340769           -0.075140   
2017-12-29  29.4365  57.528925      -0.063285           -0.111697   

            log_rtn_lag_0  log_rtn_lag_1  log_rtn_lag_2  log_rtn_lag_3  \
Date                                                                     
2017-12-22      -0.002914       0.013672      -0.003599       0.004911   
2017-12-26      -0.005202      -0.002914       0.013672      -0.003599   
2017-12-27      -0.000652      -0.005202      -0.002914       0.013672   
2017-12-28      -0.000653      -0.000652      -0.005202      -0.002914   
2017-12-29      -0.009839      -0.000653      -0.000652      -0.005202   

            log_rtn_lag_4  log_rtn_lag_5  log_rtn_lag_6  log_rtn_lag_7  \
Date                                                                     
2017-12-22       0.014546       0.011892      -0.008890      -0.016891   
2017-12-26       0.004911       0.014546       0.011892      -0.008890   
2017-12-27      -0.003599       0.004911       0.014546       0.011892   
2017-12-28       0.013672      -0.003599       0.004911       0.014546   
2017-12-29      -0.002914       0.013672      -0.003599       0.004911   

            log_rtn_lag_8  log_rtn_lag_9  log_rtn_lag_10  log_rtn_lag_11  \
Date                                                                       
2017-12-22       0.004938      -0.002308       -0.000987       -0.005904   
2017-12-26      -0.016891       0.004938       -0.002308       -0.000987   
2017-12-27      -0.008890      -0.016891        0.004938       -0.002308   
2017-12-28       0.011892      -0.008890       -0.016891        0.004938   
2017-12-29       0.014546       0.011892       -0.008890       -0.016891   

            log_rtn_lag_12  log_rtn_lag_13  log_rtn_lag_14  
Date                                                        
2017-12-22       -0.006519       -0.018668        0.021596  
2017-12-26       -0.005904       -0.006519       -0.018668  
2017-12-27       -0.000987       -0.005904       -0.006519  
2017-12-28       -0.002308       -0.000987       -0.005904  
2017-12-29        0.004938       -0.002308       -0.000987

In [15]:
y_train.tail()

Date
2017-12-22   -0.005202
2017-12-26   -0.000652
2017-12-27   -0.000653
2017-12-28   -0.009839
2017-12-29    0.002962
Name: 1d_future_log_rtn, dtype: float64

In [16]:
X_test.head()

ma50      rsi50  vol_1d_change  vol_1d_change_ma10  \
Date                                                                
2018-01-02  29.4837  57.838163       0.407924           -0.133151   
2018-01-03  29.5285  58.149105      -0.033280           -0.046269   
2018-01-04  29.5691  58.530532       0.350316            0.008641   
2018-01-05  29.6147  58.809130      -0.334217           -0.013472   
2018-01-08  29.6567  58.758780       0.292687            0.030376   

            log_rtn_lag_0  log_rtn_lag_1  log_rtn_lag_2  log_rtn_lag_3  \
Date                                                                     
2018-01-02       0.002962      -0.009839      -0.000653      -0.000652   
2018-01-03       0.002953       0.002962      -0.009839      -0.000653   
2018-01-04       0.003598       0.002953       0.002962      -0.009839   
2018-01-05       0.002608       0.003598       0.002953       0.002962   
2018-01-08      -0.000326       0.002608       0.003598       0.002953   

            log_rtn_lag_4  log_rtn_lag_5  log_rtn_lag_6  log_rtn_lag_7  \
Date                                                                     
2018-01-02      -0.005202      -0.002914       0.013672      -0.003599   
2018-01-03      -0.000652      -0.005202      -0.002914       0.013672   
2018-01-04      -0.000653      -0.000652      -0.005202      -0.002914   
2018-01-05      -0.009839      -0.000653      -0.000652      -0.005202   
2018-01-08       0.002962      -0.009839      -0.000653      -0.000652   

            log_rtn_lag_8  log_rtn_lag_9  log_rtn_lag_10  log_rtn_lag_11  \
Date                                                                       
2018-01-02       0.004911       0.014546        0.011892       -0.008890   
2018-01-03      -0.003599       0.004911        0.014546        0.011892   
2018-01-04       0.013672      -0.003599        0.004911        0.014546   
2018-01-05      -0.002914       0.013672       -0.003599        0.004911   
2018-01-08      -0.005202      -0.002914        0.013672       -0.003599   

            log_rtn_lag_12  log_rtn_lag_13  log_rtn_lag_14  
Date                                                        
2018-01-02       -0.016891        0.004938       -0.002308  
2018-01-03       -0.008890       -0.016891        0.004938  
2018-01-04        0.011892       -0.008890       -0.016891  
2018-01-05        0.014546        0.011892       -0.008890  
2018-01-08        0.004911        0.014546        0.011892

In [17]:
y_test.head()

Date
2018-01-02    0.002953
2018-01-03    0.003598
2018-01-04    0.002608
2018-01-05   -0.000326
2018-01-08    0.017757
Name: 1d_future_log_rtn, dtype: float64

# Step5 Modeling

## 5.1) Random Forest regressor

#### GridSearchCV with 1260 days training window (5 years)

In [18]:
# Code modified from book "Python for Finance"
# Define the sliding window validation and print the indices of the folds
sliding_cv = TimeSeriesSplit(n_splits=5, test_size=25, max_train_size=1260)

for fold, (main_ind, valid_ind) in enumerate(sliding_cv.split(X_train)):
    print(f"Fold {fold} ----")
    print(f"Main indices: {main_ind}")
    print(f"Valid indices: {valid_ind}")

Fold 0 ----
Main indices: [ 123  124  125 ... 1380 1381 1382]
Valid indices: [1383 1384 1385 1386 1387 1388 1389 1390 1391 1392 1393 1394 1395 1396
 1397 1398 1399 1400 1401 1402 1403 1404 1405 1406 1407]
Fold 1 ----
Main indices: [ 148  149  150 ... 1405 1406 1407]
Valid indices: [1408 1409 1410 1411 1412 1413 1414 1415 1416 1417 1418 1419 1420 1421
 1422 1423 1424 1425 1426 1427 1428 1429 1430 1431 1432]
Fold 2 ----
Main indices: [ 173  174  175 ... 1430 1431 1432]
Valid indices: [1433 1434 1435 1436 1437 1438 1439 1440 1441 1442 1443 1444 1445 1446
 1447 1448 1449 1450 1451 1452 1453 1454 1455 1456 1457]
Fold 3 ----
Main indices: [ 198  199  200 ... 1455 1456 1457]
Valid indices: [1458 1459 1460 1461 1462 1463 1464 1465 1466 1467 1468 1469 1470 1471
 1472 1473 1474 1475 1476 1477 1478 1479 1480 1481 1482]
Fold 4 ----
Main indices: [ 223  224  225 ... 1480 1481 1482]
Valid indices: [1483 1484 1485 1486 1487 1488 1489 1490 1491 1492 1493 1494 1495 1496
 1497 1498 1499 1500 1501 1502 1

In [19]:
n_estimators = [50, 100, 250, 500]
max_features = ['auto', 0.1, 0.3, 0.5]
max_depth = [1, 2, 5, 10, 20, None] 

print(n_estimators)
print(max_features)
print(max_depth)

grid = {'n_estimators': n_estimators, 
        'max_features': max_features,
        'max_depth': max_depth
        }
grid

[50, 100, 250, 500]
['auto', 0.1, 0.3, 0.5]
[1, 2, 5, 10, 20, None]


{'n_estimators': [50, 100, 250, 500],
 'max_features': ['auto', 0.1, 0.3, 0.5],
 'max_depth': [1, 2, 5, 10, 20, None]}

In [20]:
# GridSearchCV for "R_squared"
rf = RandomForestRegressor(random_state=12)

gs = GridSearchCV(estimator = rf,
                  param_grid = grid,
                  cv=sliding_cv,
                  n_jobs=-1
                  ) # Default scoring is R-square
gs_fit = gs.fit(X_train, y_train)
pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)[0:50]

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
53       0.391950      0.011906         0.016590        0.003936   
69       0.593547      0.020625         0.014706        0.001847   
70       1.541182      0.056083         0.031647        0.001522   
32       0.782048      0.028943         0.010779        0.006336   
4        0.092354      0.007489         0.005200        0.005784   
5        0.185170      0.011313         0.006251        0.007656   
54       0.999065      0.037847         0.031326        0.009884   
88       1.053350      0.030351         0.006853        0.008447   
36       0.132865      0.009343         0.007703        0.006466   
28       0.211551      0.006865         0.006251        0.007656   
7        0.927400      0.062868         0.049798        0.011412   
68       0.276439      0.012505         0.012502        0.006251   
12       0.160159      0.015760         0.009858        0.006625   
6        0.439501      0.019905         0.025121        0.007573   
52       0.188770      0.008504         0.003206        0.006412   
24       0.164601      0.016090         0.007246        0.004827   
20       0.089837      0.006918         0.007216        0.007094   
8        0.135086      0.007781         0.006250        0.007655   
9        0.285568      0.044502         0.011078        0.006185   
37       0.226412      0.013738         0.010157        0.006072   
38       0.590420      0.025836         0.022041        0.007692   
23       0.931162      0.047058         0.040730        0.009433   
13       0.320891      0.013259         0.006536        0.007401   
10       0.641950      0.041477         0.022638        0.013305   
0        1.876390      0.063891         0.009468        0.018936   
21       0.193558      0.006978         0.014755        0.001878   
11       1.263703      0.078994         0.045350        0.010223   
1        2.070254      0.100903         0.009716        0.007399   
14       0.811277      0.044255         0.023613        0.010432   
39       1.171180      0.026882         0.047803        0.011648   
44       0.441661      0.040022         0.001399        0.002798   
22       0.462021      0.026321         0.023466        0.006783   
17       0.772755      0.033953         0.011298        0.002481   
15       1.464746      0.071915         0.033837        0.006017   
29       0.470500      0.010005         0.009379        0.007658   
25       0.314937      0.028233         0.004923        0.006135   
27       1.575731      0.057242         0.035178        0.010425   
42       1.436673      0.017707         0.016729        0.003793   
2        1.830115      0.850339         0.020861        0.006611   
26       0.752628      0.025222         0.017911        0.010849   
33       1.612375      0.038655         0.010087        0.006892   
16       0.420151      0.020543         0.002104        0.004208   
3        2.469635      0.126614         0.049587        0.011592   
43       2.782187      0.071433         0.036610        0.007607   
30       1.117950      0.029020         0.015314        0.000647   
18       1.872027      0.080633         0.019197        0.006671   
31       2.235136      0.069550         0.038825        0.006981   
41       0.598486      0.021955         0.017867        0.004471   
19       3.806668      0.167955         0.042315        0.006207   
34       4.127001      0.043116         0.023265        0.006487   

   param_max_depth param_max_features param_n_estimators  \
53              10                0.1                100   
69              20                0.1                100   
70              20                0.1                250   
32               5               auto                 50   
4                1                0.1                 50   
5                1                0.1                100   
54              10                0.1                250   
88            None                0.3                 5

In [21]:
# GridSearchCV for "neg_mean_squared_error"
rf = RandomForestRegressor(random_state=12)

gs = GridSearchCV(estimator = rf,
                  param_grid = grid,
                  cv=sliding_cv,
                  n_jobs=-1,
                  scoring='neg_mean_squared_error')
gs_fit = gs.fit(X_train, y_train)
pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)[0:10]

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
69       0.540632      0.007760         0.012386        0.006198   
70       1.341600      0.033496         0.023849        0.006917   
53       0.416638      0.012031         0.012000        0.002334   
52       0.192237      0.011104         0.007609        0.000371   
68       0.256015      0.010663         0.010581        0.006474   
32       0.801801      0.031742         0.009107        0.003508   
28       0.218043      0.006136         0.008699        0.007200   
4        0.075546      0.006172         0.009380        0.007659   
44       0.463373      0.015115         0.002603        0.003327   
24       0.169833      0.008409         0.004734        0.006699   

   param_max_depth param_max_features param_n_estimators  \
69              20                0.1                100   
70              20                0.1                250   
53              10                0.1                100   
52              10                0.1                 50   
68              20                0.1                 50   
32               5               auto                 50   
28               2                0.5                 50   
4                1                0.1                 50   
44               5                0.5                 50   
24               2                0.3                 50   

                                               params  split0_test_score  \
69  {'max_depth': 20, 'max_features': 0.1, 'n_esti...          -0.000097   
70  {'max_depth': 20, 'max_features': 0.1, 'n_esti...          -0.000092   
53  {'max_depth': 10, 'max_features': 0.1, 'n_esti...          -0.000092   
52  {'max_depth': 10, 'max_features': 0.1, 'n_esti...          -0.000089   
68  {'max_depth': 20, 'max_features': 0.1, 'n_esti...          -0.000100   
32  {'max_depth': 5, 'max_features': 'auto', 'n_es...          -0.000088   
28  {'max_depth': 2, 'max_features': 0.5, 'n_estim...          -0.000089   
4   {'max_depth': 1, 'max_features': 0.1, 'n_estim...          -0.000089   
44  {'max_depth': 5, 'max_features': 0.5, 'n_estim...          -0.000088   
24  {'max_depth': 2, 'max_features': 0.3, 'n_estim...          -0.000089   

    split1_test_score  split2_test_score  split3_test_score  \
69          -0.000215          -0.000071          -0.000083   
70          -0.000212          -0.000071          -0.000084   
53          -0.000214          -0.000064          -0.000092   
52          -0.000214          -0.000071          -0.000092   
68          -0.000225          -0.000073          -0.000075   
32          -0.000216          -0.000068          -0.000095   
28          -0.000215          -0.000068          -0.000095   
4           -0.000216          -0.000067          -0.000095   
44          -0.000215          -0.000070          -0.000095   
24          -0.000215          -0.000068          -0.000095   

    split4_test_score  mean_test_score  std_test_score  rank_test_score  
69          -0.000175        -0.000128        0.000057                1  
70          -0.000185        -0.000129        0.000058                2  
53          -0.000182        -0.000129        0.000058                3  
52          -0.000178        -0.000129        0.000057                4  
68          -0.000172        -0.000129        0.000060                5  
32          -0.000179        -0.000129        0.000058                6  
28          -0.000180        -0.000129        0.000057                7  
4           -0.000181        -0.000129        0.000058                8  
44          -0.000179        -0.000130        0.000057                9  
24          -0.000181        -0.000130        0.000058               10

In [22]:
# Take best parameters
gs_fit.best_params_

{'max_depth': 20, 'max_features': 0.1, 'n_estimators': 100}

#### Test performance and check for sign of overfitting

In [ ]:
# Estimate model with best hyperparameters for 1260 days (5 years) before test set 

In [23]:
len(X_train)

1508

In [24]:
len(X_train.iloc[-1260:, :])

1260

In [25]:
X_train.iloc[-1260:, :].tail()

ma50      rsi50  vol_1d_change  vol_1d_change_ma10  \
Date                                                                
2017-12-22  29.2411  59.868957      -0.497860           -0.135801   
2017-12-26  29.2917  59.128890      -0.285393           -0.090914   
2017-12-27  29.3437  59.035808       0.126103           -0.106589   
2017-12-28  29.3891  58.941127       0.340769           -0.075140   
2017-12-29  29.4365  57.528925      -0.063285           -0.111697   

            log_rtn_lag_0  log_rtn_lag_1  log_rtn_lag_2  log_rtn_lag_3  \
Date                                                                     
2017-12-22      -0.002914       0.013672      -0.003599       0.004911   
2017-12-26      -0.005202      -0.002914       0.013672      -0.003599   
2017-12-27      -0.000652      -0.005202      -0.002914       0.013672   
2017-12-28      -0.000653      -0.000652      -0.005202      -0.002914   
2017-12-29      -0.009839      -0.000653      -0.000652      -0.005202   

            log_rtn_lag_4  log_rtn_lag_5  log_rtn_lag_6  log_rtn_lag_7  \
Date                                                                     
2017-12-22       0.014546       0.011892      -0.008890      -0.016891   
2017-12-26       0.004911       0.014546       0.011892      -0.008890   
2017-12-27      -0.003599       0.004911       0.014546       0.011892   
2017-12-28       0.013672      -0.003599       0.004911       0.014546   
2017-12-29      -0.002914       0.013672      -0.003599       0.004911   

            log_rtn_lag_8  log_rtn_lag_9  log_rtn_lag_10  log_rtn_lag_11  \
Date                                                                       
2017-12-22       0.004938      -0.002308       -0.000987       -0.005904   
2017-12-26      -0.016891       0.004938       -0.002308       -0.000987   
2017-12-27      -0.008890      -0.016891        0.004938       -0.002308   
2017-12-28       0.011892      -0.008890       -0.016891        0.004938   
2017-12-29       0.014546       0.011892       -0.008890       -0.016891   

            log_rtn_lag_12  log_rtn_lag_13  log_rtn_lag_14  
Date                                                        
2017-12-22       -0.006519       -0.018668        0.021596  
2017-12-26       -0.005904       -0.006519       -0.018668  
2017-12-27       -0.000987       -0.005904       -0.006519  
2017-12-28       -0.002308       -0.000987       -0.005904  
2017-12-29        0.004938       -0.002308       -0.000987

In [26]:
# Estimate model with best hyperparameters for 1260 days (5 years) before test set 
rf = RandomForestRegressor(n_estimators=100, max_features=0.1, max_depth=20, random_state=12)

In [27]:
rf.fit(X_train.iloc[-1260:, :], y_train.iloc[-1260:])
print(rf.score(X_train.iloc[-1260:, :], y_train.iloc[-1260:]))

0.760625043111836


In [28]:
print(rf.score(X_test, y_test))

-0.028933477904770077


In [29]:
# Train performance 
y_train_pred = rf.predict(X_train.iloc[-1260:, :])
print('Train r-square                    :', r2_score(y_train.iloc[-1260:], y_train_pred))
print('Train mean_squared_error          :', mean_squared_error(y_train.iloc[-1260:], y_train_pred))
print('Train roof of mean_squared_error  :', np.sqrt(mean_squared_error(y_train.iloc[-1260:], y_train_pred)))
print('Train mean_absolute_error         :', mean_absolute_error(y_train.iloc[-1260:], y_train_pred))

Train r-square                    : 0.760625043111836
Train mean_squared_error          : 5.112368764933299e-05
Train roof of mean_squared_error  : 0.007150083051918557
Train mean_absolute_error         : 0.005449516077613446


In [30]:
# Test performance 
y_test_pred = rf.predict(X_test)
print('Test r-square                    :', r2_score(y_test, y_test_pred))
print('Test mean_squared_error          :', mean_squared_error(y_test, y_test_pred))
print('Test roof of mean_squared_error  :', np.sqrt(mean_squared_error(y_test, y_test_pred)))
print('Test mean_absolute_error         :', mean_absolute_error(y_test, y_test_pred))

Test r-square                    : -0.028933477904770077
Test mean_squared_error          : 0.00015329974511170676
Test roof of mean_squared_error  : 0.012381427426258524
Test mean_absolute_error         : 0.009517750093810113


In [31]:
# Compared with default RandomeForest 
rf = RandomForestRegressor(random_state=12)
rf.fit(X_train.iloc[-1260:, :], y_train.iloc[-1260:])
print(rf.score(X_train.iloc[-1260:, :], y_train.iloc[-1260:]))

0.8525284382165186


In [32]:
print(rf.score(X_test, y_test))

-0.005177855456341973


#### GridSearchCV with 756 days training window (3 years)

In [33]:
# Define sliding window with 756 days 
sliding_cv = TimeSeriesSplit(n_splits=5, test_size=25, max_train_size=756)

In [34]:
grid

{'n_estimators': [50, 100, 250, 500],
 'max_features': ['auto', 0.1, 0.3, 0.5],
 'max_depth': [1, 2, 5, 10, 20, None]}

In [35]:
# GridSearchCV for "neg_mean_squared_error"
rf = RandomForestRegressor(random_state=12)

gs = GridSearchCV(estimator = rf,
                  param_grid = grid,
                  cv=sliding_cv,
                  n_jobs=-1,
                  scoring='neg_mean_squared_error')
gs_fit = gs.fit(X_train, y_train)
pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)[0:10]

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
7        0.966210      0.037325         0.051274        0.008355   
5        0.190090      0.004048         0.011801        0.002399   
4        0.100444      0.014336         0.008198        0.002926   
31       1.681116      0.049854         0.041447        0.008371   
6        0.453435      0.033746         0.024406        0.004033   
23       0.933316      0.042029         0.051482        0.012037   
19       2.872257      0.066400         0.049681        0.012727   
27       1.334442      0.059146         0.039411        0.010197   
29       0.371539      0.014598         0.007659        0.007000   
1        0.361918      0.012967         0.011406        0.001356   

   param_max_depth param_max_features param_n_estimators  \
7                1                0.1                500   
5                1                0.1                100   
4                1                0.1                 50   
31               2                0.5                500   
6                1                0.1                250   
23               2                0.1                500   
19               2               auto                500   
27               2                0.3                500   
29               2                0.5                100   
1                1               auto                100   

                                               params  split0_test_score  \
7   {'max_depth': 1, 'max_features': 0.1, 'n_estim...          -0.000089   
5   {'max_depth': 1, 'max_features': 0.1, 'n_estim...          -0.000089   
4   {'max_depth': 1, 'max_features': 0.1, 'n_estim...          -0.000089   
31  {'max_depth': 2, 'max_features': 0.5, 'n_estim...          -0.000089   
6   {'max_depth': 1, 'max_features': 0.1, 'n_estim...          -0.000090   
23  {'max_depth': 2, 'max_features': 0.1, 'n_estim...          -0.000089   
19  {'max_depth': 2, 'max_features': 'auto', 'n_es...          -0.000089   
27  {'max_depth': 2, 'max_features': 0.3, 'n_estim...          -0.000089   
29  {'max_depth': 2, 'max_features': 0.5, 'n_estim...          -0.000090   
1   {'max_depth': 1, 'max_features': 'auto', 'n_es...          -0.000090   

    split1_test_score  split2_test_score  split3_test_score  \
7           -0.000216          -0.000067          -0.000096   
5           -0.000216          -0.000067          -0.000095   
4           -0.000216          -0.000068          -0.000096   
31          -0.000216          -0.000069          -0.000095   
6           -0.000216          -0.000067          -0.000096   
23          -0.000215          -0.000068          -0.000096   
19          -0.000216          -0.000069          -0.000096   
27          -0.000216          -0.000068          -0.000096   
29          -0.000217          -0.000068          -0.000095   
1           -0.000217          -0.000068          -0.000096   

    split4_test_score  mean_test_score  std_test_score  rank_test_score  
7           -0.000182         -0.00013        0.000058                1  
5           -0.000182         -0.00013        0.000058                2  
4           -0.000182         -0.00013        0.000058                3  
31          -0.000182         -0.00013        0.000058                4  
6           -0.000183         -0.00013        0.000058                5  
23          -0.000183         -0.00013        0.000058                6  
19          -0.000181         -0.00013        0.000057                7  
27          -0.000183         -0.00013        0.000058                8  
29          -0.000182         -0.00013        0.000058                9  
1           -0.000181         -0.00013        0.000058               10

In [36]:
# Take best parameters
gs_fit.best_params_

{'max_depth': 1, 'max_features': 0.1, 'n_estimators': 500}

## 5.2) Gradient boosting regressor

#### GridSearchCV with 1260 days training window (5 years)

In [37]:
# Define the sliding window validation with 1260 days
sliding_cv = TimeSeriesSplit(n_splits=5, test_size=25, max_train_size=1260)

In [38]:
grid = {
    'learning_rate': [0.05, 0.1, 0.15],
    'n_estimators': [50, 100, 150],
    'subsample': [0.8, 1],
    'max_depth': [3, 6, 9, 12, 15],
    'min_samples_split': [2, 6, 10],
    'max_features': ['auto', 0.1, 0.3, 0.5]
    }
grid

{'learning_rate': [0.05, 0.1, 0.15],
 'n_estimators': [50, 100, 150],
 'subsample': [0.8, 1],
 'max_depth': [3, 6, 9, 12, 15],
 'min_samples_split': [2, 6, 10],
 'max_features': ['auto', 0.1, 0.3, 0.5]}

In [39]:
# GridSearchCV for "neg_mean_squared_error"
start = time.time()
gb = GradientBoostingRegressor(random_state=12)

gs = GridSearchCV(estimator = gb,
                  param_grid = grid,
                  cv=sliding_cv,
                  n_jobs=-1,
                  scoring='neg_mean_squared_error')
gs_fit = gs.fit(X_train, y_train)
pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)[0:20]

end = time.time()
tune_time = (end - start)

In [40]:
tune_time

1002.1249730587006

In [41]:
pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)[0:20]

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
421       0.545195      0.026331         0.000000        0.000000   
18        0.067573      0.006132         0.000000        0.000000   
31        0.078498      0.009884         0.000000        0.000000   
20        0.135052      0.012640         0.003125        0.006250   
25        0.078280      0.012907         0.003125        0.006250   
37        0.226274      0.008177         0.003125        0.006250   
96        0.130650      0.010201         0.001002        0.001266   
390       0.126736      0.003818         0.002801        0.000401   
108       0.482624      0.044261         0.001598        0.001355   
427       0.498541      0.012650         0.009775        0.007191   
30        0.086039      0.007028         0.000000        0.000000   
42        0.210411      0.021041         0.000000        0.000000   
19        0.075366      0.008758         0.003103        0.006207   
751       0.120864      0.008702         0.002807        0.000403   
48        0.200868      0.006250         0.006250        0.007655   
66        0.332882      0.012854         0.003125        0.006249   
102       0.137841      0.007606         0.001401        0.001200   
6         0.591284      0.020523         0.000000        0.000000   
24        0.084023      0.017179         0.000000        0.000000   
1         2.445959      0.070818         0.003125        0.006250   

    param_learning_rate param_max_depth param_max_features  \
421                 0.1               3                0.5   
18                 0.05               3                0.1   
31                 0.05               3                0.1   
20                 0.05               3                0.1   
25                 0.05               3                0.1   
37                 0.05               3                0.3   
96                 0.05               6                0.1   
390                 0.1               3                0.1   
108                0.05               6                0.3   
427                 0.1               3                0.5   
30                 0.05               3                0.1   
42                 0.05               3                0.3   
19                 0.05               3                0.1   
751                0.15               3                0.1   
48                 0.05               3                0.3   
66                 0.05               3                0.5   
102                0.05               6                0.1   
6                  0.05               3               auto   
24                 0.05               3                0.1   
1                  0.05               3               auto   

    param_min_samples_split param_n_estimators param_subsample  \
421                       6                 50               1   
18                        2                 50             0.8   
31                       10                 50               1   
20                        2                100             0.8   
25                        6                 50               1   
37                        2                 50               1   
96                        6                 50             0.8   
390                      10                 50             0.8   
108                       2                 50             0.8   
427                      10                 50               1   
30                       10                 50             0.8   
42                        6                 50             0.8   
19                        2                 50               1   
751                      10                 50               1   
48                       10                 50             0.8   
66                       10                 50             0.8   
102                      10                 50             0.8   
6                         6                 50             0.8  

In [42]:
# Take best parameters
gs_fit.best_params_

{'learning_rate': 0.1,
 'max_depth': 3,
 'max_features': 0.5,
 'min_samples_split': 6,
 'n_estimators': 50,
 'subsample': 1}

In [43]:
# Second sweep with finer learning rate
grid = {
    'learning_rate': [0.07, 0.08, 0.09, 0.1, 0.11, 0.12, 0.13],
    'n_estimators': [50],
    'subsample': [1],
    'max_depth': [3],
    'min_samples_split': [6],
    'max_features': ['auto', 0.1, 0.3, 0.5]
    }
grid

{'learning_rate': [0.07, 0.08, 0.09, 0.1, 0.11, 0.12, 0.13],
 'n_estimators': [50],
 'subsample': [1],
 'max_depth': [3],
 'min_samples_split': [6],
 'max_features': ['auto', 0.1, 0.3, 0.5]}

In [44]:
# GridSearchCV for "neg_mean_squared_error"
start = time.time()
gb = GradientBoostingRegressor(random_state=12)

gs = GridSearchCV(estimator = gb,
                  param_grid = grid,
                  cv=sliding_cv,
                  n_jobs=-1,
                  scoring='neg_mean_squared_error')
gs_fit = gs.fit(X_train, y_train)

end = time.time()
tune_time = (end - start)
print(tune_time)

pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)[0:20]

9.401136875152588


mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
5        0.082190      0.007712         0.005658        0.006820   
15       0.384735      0.012086         0.006789        0.008358   
10       0.240998      0.008008         0.001814        0.001073   
9        0.080809      0.016370         0.000000        0.000000   
1        0.078826      0.016321         0.000000        0.000000   
25       0.074623      0.006376         0.003126        0.006252   
3        0.372613      0.013061         0.002977        0.004267   
26       0.229467      0.014213         0.000401        0.000801   
21       0.085773      0.010230         0.002602        0.003328   
13       0.081583      0.009979         0.002000        0.002190   
2        0.249953      0.020198         0.000400        0.000801   
0        0.775644      0.034208         0.000142        0.000283   
17       0.075218      0.002406         0.002303        0.003688   
11       0.385715      0.018253         0.000400        0.000801   
4        0.800499      0.044791         0.005272        0.006639   
6        0.233580      0.006851         0.000000        0.000000   
22       0.232008      0.005910         0.000653        0.000833   
19       0.387171      0.019113         0.000000        0.000000   
23       0.392317      0.026598         0.003125        0.006251   
8        0.793900      0.027795         0.003536        0.006120   

   param_learning_rate param_max_depth param_max_features  \
5                 0.08               3                0.1   
15                 0.1               3                0.5   
10                0.09               3                0.3   
9                 0.09               3                0.1   
1                 0.07               3                0.1   
25                0.13               3                0.1   
3                 0.07               3                0.5   
26                0.13               3                0.3   
21                0.12               3                0.1   
13                 0.1               3                0.1   
2                 0.07               3                0.3   
0                 0.07               3               auto   
17                0.11               3                0.1   
11                0.09               3                0.5   
4                 0.08               3               auto   
6                 0.08               3                0.3   
22                0.12               3                0.3   
19                0.11               3                0.5   
23                0.12               3                0.5   
8                 0.09               3               auto   

   param_min_samples_split param_n_estimators param_subsample  \
5                        6                 50               1   
15                       6                 50               1   
10                       6                 50               1   
9                        6                 50               1   
1                        6                 50               1   
25                       6                 50               1   
3                        6                 50               1   
26                       6                 50               1   
21                       6                 50               1   
13                       6                 50               1   
2                        6                 50               1   
0                        6                 50               1   
17                       6                 50               1   
11                       6                 50               1   
4                        6                 50               1   
6                        6                 50               1   
22                       6                 50               1   
19                       6                 50               1   
23                       6                 50             

In [45]:
# Take best parameters
gs_fit.best_params_

{'learning_rate': 0.08,
 'max_depth': 3,
 'max_features': 0.1,
 'min_samples_split': 6,
 'n_estimators': 50,
 'subsample': 1}

#### Test performance and check for sign of overfitting

In [46]:
# Estimate model with best hyperparameters for 1260 days (5 years) before test set 
gb = GradientBoostingRegressor(learning_rate=0.08, max_depth=3, max_features=0.1, min_samples_split=6,
        n_estimators=50, subsample=1, random_state=12)

In [47]:
gb.fit(X_train.iloc[-1260:, :], y_train.iloc[-1260:])
print(gb.score(X_train.iloc[-1260:, :], y_train.iloc[-1260:]))

0.17142936172839374


In [48]:
print(gb.score(X_test, y_test))

0.006560755611047853


In [49]:
# Train performance 
y_train_pred = gb.predict(X_train.iloc[-1260:, :])
print('Train r-square                    :', r2_score(y_train.iloc[-1260:], y_train_pred))
print('Train mean_squared_error          :', mean_squared_error(y_train.iloc[-1260:], y_train_pred))
print('Train roof of mean_squared_error  :', np.sqrt(mean_squared_error(y_train.iloc[-1260:], y_train_pred)))
print('Train mean_absolute_error         :', mean_absolute_error(y_train.iloc[-1260:], y_train_pred))

Train r-square                    : 0.17142936172839374
Train mean_squared_error          : 0.00017695913999139207
Train roof of mean_squared_error  : 0.013302598993858007
Train mean_absolute_error         : 0.009918073564894618


In [50]:
# Test performance 
y_test_pred = gb.predict(X_test)
print('Test r-square                    :', r2_score(y_test, y_test_pred))
print('Test mean_squared_error          :', mean_squared_error(y_test, y_test_pred))
print('Test roof of mean_squared_error  :', np.sqrt(mean_squared_error(y_test, y_test_pred)))
print('Test mean_absolute_error         :', mean_absolute_error(y_test, y_test_pred))

Test r-square                    : 0.006560755611047853
Test mean_squared_error          : 0.00014801149561088345
Test roof of mean_squared_error  : 0.012165997518119238
Test mean_absolute_error         : 0.00939260639772379


## 5.3) Ridge regression

#### GridSearchCV with 1260 days training window (5 years), without month sine and cosine

In [51]:
alpha = [n for n in np.logspace(-5, 2, num=20, endpoint=True, base=10.0)]
alpha

[1e-05,
 2.3357214690901213e-05,
 5.4555947811685143e-05,
 0.00012742749857031334,
 0.00029763514416313193,
 0.0006951927961775605,
 0.001623776739188721,
 0.00379269019073225,
 0.008858667904100823,
 0.02069138081114788,
 0.04832930238571752,
 0.11288378916846883,
 0.26366508987303555,
 0.6158482110660255,
 1.438449888287663,
 3.359818286283781,
 7.847599703514606,
 18.32980710832434,
 42.81332398719387,
 100.0]

In [52]:
pipe = make_pipeline(
    StandardScaler(), 
    Ridge()
)

In [53]:
sliding_cv

TimeSeriesSplit(gap=0, max_train_size=1260, n_splits=5, test_size=25)

In [54]:
# GridSearchCV
param = {'ridge__alpha': alpha}

gs = GridSearchCV(estimator = pipe,
                  param_grid = param,
                  cv = sliding_cv,
                  n_jobs = -1,
                  scoring = 'neg_mean_squared_error')
gs_fit = gs.fit(X_train, y_train)
pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
19       0.012501      0.006251         0.000000        0.000000   
18       0.006251      0.007656         0.000000        0.000000   
17       0.006252      0.007657         0.003126        0.006252   
16       0.003129      0.006257         0.006252        0.007657   
15       0.006257      0.007664         0.000000        0.000000   
14       0.006416      0.007858         0.003129        0.006257   
13       0.000000      0.000000         0.005409        0.006624   
12       0.009373      0.007653         0.003124        0.006249   
11       0.009375      0.007655         0.000000        0.000000   
10       0.000000      0.000000         0.003125        0.006250   
9        0.009371      0.007652         0.000000        0.000000   
8        0.000000      0.000000         0.000000        0.000000   
7        0.009370      0.007650         0.003123        0.006247   
6        0.009404      0.007678         0.003123        0.006247   
5        0.008258      0.004968         0.000000        0.000000   
4        0.010770      0.003968         0.001708        0.003416   
3        0.009376      0.007655         0.003125        0.006250   
2        0.015637      0.009885         0.006252        0.007658   
1        0.018894      0.005047         0.000000        0.000000   
0        0.025738      0.008187         0.009388        0.007665   

   param_ridge__alpha                                    params  \
19              100.0                   {'ridge__alpha': 100.0}   
18          42.813324       {'ridge__alpha': 42.81332398719387}   
17          18.329807       {'ridge__alpha': 18.32980710832434}   
16             7.8476       {'ridge__alpha': 7.847599703514606}   
15           3.359818       {'ridge__alpha': 3.359818286283781}   
14            1.43845       {'ridge__alpha': 1.438449888287663}   
13           0.615848      {'ridge__alpha': 0.6158482110660255}   
12           0.263665     {'ridge__alpha': 0.26366508987303555}   
11           0.112884     {'ridge__alpha': 0.11288378916846883}   
10           0.048329     {'ridge__alpha': 0.04832930238571752}   
9            0.020691     {'ridge__alpha': 0.02069138081114788}   
8            0.008859    {'ridge__alpha': 0.008858667904100823}   
7            0.003793     {'ridge__alpha': 0.00379269019073225}   
6            0.001624    {'ridge__alpha': 0.001623776739188721}   
5            0.000695   {'ridge__alpha': 0.0006951927961775605}   
4            0.000298  {'ridge__alpha': 0.00029763514416313193}   
3            0.000127  {'ridge__alpha': 0.00012742749857031334}   
2            0.000055  {'ridge__alpha': 5.4555947811685143e-05}   
1            0.000023  {'ridge__alpha': 2.3357214690901213e-05}   
0             0.00001                   {'ridge__alpha': 1e-05}   

    split0_test_score  split1_test_score  split2_test_score  \
19          -0.000097          -0.000216          -0.000068   
18          -0.000097          -0.000216          -0.000069   
17          -0.000097          -0.000216          -0.000069   
16          -0.000097          -0.000217          -0.000069   
15          -0.000097          -0.000217          -0.000069   
14          -0.000098          -0.000217          -0.000069   
13          -0.000098          -0.000217          -0.000069   
12          -0.000098          -0.000217          -0.000069   
11          -0.000098          -0.000217          -0.000069   
10          -0.000098          -0.000217          -0.000069   
9           -0.000098          -0.000217          -0.000069   
8           -0.000098          -0.000217          -0.000069   
7           -0.000098          -0.000217          -0.000069   
6           -0.000098          -0.000217          -0.000069   
5           -0.000098          -0.000217          -0.000069   
4           -0.000098          -0.000217          -0.000069   
3           -0.000098          -0.000217          -0.000069   
2           -0.000098          -0

In [55]:
# Take best parameters
gs_fit.best_params_

{'ridge__alpha': 100.0}

Sweep 2

In [56]:
# Let investigate for bigger value of alpha
alpha = [n for n in np.logspace(1, 8, num=8, endpoint=True, base=10.0)]
alpha

[10.0, 100.0, 1000.0, 10000.0, 100000.0, 1000000.0, 10000000.0, 100000000.0]

In [57]:
# GridSearchCV
param = {'ridge__alpha': alpha}

gs = GridSearchCV(estimator = pipe,
                  param_grid = param,
                  cv = sliding_cv,
                  n_jobs = -1,
                  scoring = 'neg_mean_squared_error')
gs_fit = gs.fit(X_train, y_train)
pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
4       0.000515      0.001031         0.000000        0.000000   
5       0.012432      0.006362         0.001399        0.000828   
6       0.004399      0.001179         0.001001        0.000061   
7       0.005269      0.000434         0.001810        0.000421   
3       0.006063      0.003957         0.001788        0.002495   
2       0.005576      0.000511         0.001401        0.000801   
1       0.004935      0.000220         0.001799        0.000412   
0       0.004918      0.001026         0.001948        0.000400   

  param_ridge__alpha                         params  split0_test_score  \
4           100000.0     {'ridge__alpha': 100000.0}          -0.000089   
5          1000000.0    {'ridge__alpha': 1000000.0}          -0.000089   
6         10000000.0   {'ridge__alpha': 10000000.0}          -0.000089   
7        100000000.0  {'ridge__alpha': 100000000.0}          -0.000089   
3            10000.0      {'ridge__alpha': 10000.0}          -0.000089   
2             1000.0       {'ridge__alpha': 1000.0}          -0.000093   
1              100.0        {'ridge__alpha': 100.0}          -0.000097   
0               10.0         {'ridge__alpha': 10.0}          -0.000097   

   split1_test_score  split2_test_score  split3_test_score  split4_test_score  \
4          -0.000218          -0.000066          -0.000096          -0.000181   
5          -0.000218          -0.000066          -0.000096          -0.000181   
6          -0.000218          -0.000066          -0.000096          -0.000181   
7          -0.000218          -0.000066          -0.000096          -0.000181   
3          -0.000218          -0.000066          -0.000096          -0.000182   
2          -0.000216          -0.000067          -0.000094          -0.000186   
1          -0.000216          -0.000068          -0.000094          -0.000192   
0          -0.000217          -0.000069          -0.000093          -0.000194   

   mean_test_score  std_test_score  rank_test_score  
4        -0.000130        0.000059                1  
5        -0.000130        0.000059                2  
6        -0.000130        0.000059                3  
7        -0.000130        0.000059                4  
3        -0.000130        0.000059                5  
2        -0.000131        0.000059                6  
1        -0.000133        0.000059                7  
0        -0.000134        0.000059                8

In [ ]:
# Seem like between e4 and e8 

Sweep 3

In [58]:
alpha = [n for n in np.logspace(3, 8, num=20, endpoint=True, base=10.0)]
alpha

[1000.0,
 1832.9807108324355,
 3359.818286283781,
 6158.482110660267,
 11288.378916846883,
 20691.3808111479,
 37926.901907322535,
 69519.27961775605,
 127427.49857031321,
 233572.14690901214,
 428133.2398719396,
 784759.9703514606,
 1438449.888287663,
 2636650.8987303553,
 4832930.238571752,
 8858667.904100832,
 16237767.391887208,
 29763514.416313194,
 54555947.811685145,
 100000000.0]

In [59]:
param = {'ridge__alpha': alpha}

gs = GridSearchCV(estimator = pipe,
                  param_grid = param,
                  cv = sliding_cv,
                  n_jobs = -1,
                  scoring = 'neg_mean_squared_error')
gs_fit = gs.fit(X_train, y_train)
pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
6        0.007439      0.002754         0.001822        0.000411   
7        0.004767      0.000426         0.001565        0.000432   
8        0.005250      0.000339         0.001605        0.000453   
9        0.005388      0.000492         0.001802        0.000337   
10       0.004820      0.001518         0.001223        0.001000   
5        0.005776      0.002769         0.002695        0.001873   
11       0.002222      0.002735         0.000226        0.000452   
12       0.001053      0.001601         0.000000        0.000000   
13       0.006252      0.007658         0.000000        0.000000   
14       0.003126      0.006252         0.000000        0.000000   
15       0.006291      0.007705         0.003146        0.006291   
16       0.000000      0.000000         0.000000        0.000000   
17       0.006253      0.007658         0.003126        0.006253   
18       0.003124      0.006248         0.003124        0.006248   
19       0.009372      0.007652         0.000000        0.000000   
4        0.004784      0.000432         0.000777        0.000747   
3        0.010538      0.008659         0.004455        0.005936   
2        0.001086      0.001466         0.000000        0.000000   
1        0.005320      0.000531         0.000964        0.000671   
0        0.005598      0.000493         0.002000        0.000005   

   param_ridge__alpha                                params  \
6        37926.901907  {'ridge__alpha': 37926.901907322535}   
7        69519.279618   {'ridge__alpha': 69519.27961775605}   
8        127427.49857  {'ridge__alpha': 127427.49857031321}   
9       233572.146909  {'ridge__alpha': 233572.14690901214}   
10      428133.239872   {'ridge__alpha': 428133.2398719396}   
5        20691.380811    {'ridge__alpha': 20691.3808111479}   
11      784759.970351   {'ridge__alpha': 784759.9703514606}   
12     1438449.888288   {'ridge__alpha': 1438449.888287663}   
13      2636650.89873  {'ridge__alpha': 2636650.8987303553}   
14     4832930.238572   {'ridge__alpha': 4832930.238571752}   
15     8858667.904101   {'ridge__alpha': 8858667.904100832}   
16    16237767.391887  {'ridge__alpha': 16237767.391887208}   
17    29763514.416313  {'ridge__alpha': 29763514.416313194}   
18    54555947.811685  {'ridge__alpha': 54555947.811685145}   
19        100000000.0         {'ridge__alpha': 100000000.0}   
4        11288.378917  {'ridge__alpha': 11288.378916846883}   
3         6158.482111   {'ridge__alpha': 6158.482110660267}   
2         3359.818286   {'ridge__alpha': 3359.818286283781}   
1         1832.980711  {'ridge__alpha': 1832.9807108324355}   
0              1000.0              {'ridge__alpha': 1000.0}   

    split0_test_score  split1_test_score  split2_test_score  \
6           -0.000089          -0.000218          -0.000066   
7           -0.000089          -0.000218          -0.000066   
8           -0.000089          -0.000218          -0.000066   
9           -0.000089          -0.000218          -0.000066   
10          -0.000089          -0.000218          -0.000066   
5           -0.000089          -0.000218          -0.000066   
11          -0.000089          -0.000218          -0.000066   
12          -0.000089          -0.000218          -0.000066   
13          -0.000089          -0.000218          -0.000066   
14          -0.000089          -0.000218          -0.000066   
15          -0.000089          -0.000218          -0.000066   
16          -0.000089          -0.000218          -0.000066   
17          -0.000089          -0.000218          -0.000066   
18          -0.000089          -0.000218          -0.000066   
19          -0.000089          -0.000218          -0.000066   
4           -0.000089          -0.000218          -0.000066   
3           -0.000090          -0.000217          -0.000066   
2           -0.000090          -0.000217          -0.000066   
1           -0.000091          -0.000216          -0.0

In [60]:
# Take best parameters
gs_fit.best_params_

{'ridge__alpha': 37926.901907322535}

In [ ]:
# Seem like between 20000 and 120000 

Sweep 4

In [61]:
alpha = [n for n in np.linspace(20000, 120000, num=11, endpoint=True)]
alpha

[20000.0,
 30000.0,
 40000.0,
 50000.0,
 60000.0,
 70000.0,
 80000.0,
 90000.0,
 100000.0,
 110000.0,
 120000.0]

In [62]:
param = {'ridge__alpha': alpha}

gs = GridSearchCV(estimator = pipe,
                  param_grid = param,
                  cv = sliding_cv,
                  n_jobs = -1,
                  scoring = 'neg_mean_squared_error')
gs_fit = gs.fit(X_train, y_train)
pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
2        0.001117      0.001404         0.000000        0.000000   
3        0.009685      0.007928         0.004239        0.005992   
4        0.008051      0.006090         0.001587        0.000479   
1        0.006453      0.002173         0.001093        0.000822   
5        0.005320      0.000751         0.002111        0.000217   
6        0.004911      0.001095         0.001622        0.000512   
7        0.005425      0.000621         0.001983        0.000041   
8        0.005593      0.000801         0.002000        0.000007   
9        0.005626      0.000469         0.001993        0.000006   
10       0.004840      0.000431         0.001395        0.000487   
0        0.006655      0.003353         0.001800        0.002916   

   param_ridge__alpha                      params  split0_test_score  \
2             40000.0   {'ridge__alpha': 40000.0}          -0.000089   
3             50000.0   {'ridge__alpha': 50000.0}          -0.000089   
4             60000.0   {'ridge__alpha': 60000.0}          -0.000089   
1             30000.0   {'ridge__alpha': 30000.0}          -0.000089   
5             70000.0   {'ridge__alpha': 70000.0}          -0.000089   
6             80000.0   {'ridge__alpha': 80000.0}          -0.000089   
7             90000.0   {'ridge__alpha': 90000.0}          -0.000089   
8            100000.0  {'ridge__alpha': 100000.0}          -0.000089   
9            110000.0  {'ridge__alpha': 110000.0}          -0.000089   
10           120000.0  {'ridge__alpha': 120000.0}          -0.000089   
0             20000.0   {'ridge__alpha': 20000.0}          -0.000089   

    split1_test_score  split2_test_score  split3_test_score  \
2           -0.000218          -0.000066          -0.000096   
3           -0.000218          -0.000066          -0.000096   
4           -0.000218          -0.000066          -0.000096   
1           -0.000218          -0.000066          -0.000096   
5           -0.000218          -0.000066          -0.000096   
6           -0.000218          -0.000066          -0.000096   
7           -0.000218          -0.000066          -0.000096   
8           -0.000218          -0.000066          -0.000096   
9           -0.000218          -0.000066          -0.000096   
10          -0.000218          -0.000066          -0.000096   
0           -0.000218          -0.000066          -0.000096   

    split4_test_score  mean_test_score  std_test_score  rank_test_score  
2           -0.000181         -0.00013        0.000059                1  
3           -0.000181         -0.00013        0.000059                2  
4           -0.000181         -0.00013        0.000059                3  
1           -0.000181         -0.00013        0.000059                4  
5           -0.000181         -0.00013        0.000059                5  
6           -0.000181         -0.00013        0.000059                6  
7           -0.000181         -0.00013        0.000059                7  
8           -0.000181         -0.00013        0.000059                8  
9           -0.000181         -0.00013        0.000059                9  
10          -0.000181         -0.00013        0.000059               10  
0           -0.000182         -0.00013        0.000059               11

In [63]:
# Take best parameters
gs_fit.best_params_

{'ridge__alpha': 40000.0}

#### Test performance and check for sign of overfitting

In [64]:
pipe = make_pipeline(
    StandardScaler(), 
    Ridge(alpha=40000)
)

In [65]:
pipe.fit(X_train.iloc[-1260:, :], y_train.iloc[-1260:])
print(pipe.score(X_train.iloc[-1260:, :], y_train.iloc[-1260:]))

0.0007114552003412156


In [66]:
print(pipe.score(X_test, y_test))

-0.020435722725925753


In [67]:
# Train performance 
y_train_pred = pipe.predict(X_train.iloc[-1260:, :])
print('Train r-square                    :', r2_score(y_train.iloc[-1260:], y_train_pred))
print('Train mean_squared_error          :', mean_squared_error(y_train.iloc[-1260:], y_train_pred))
print('Train roof of mean_squared_error  :', np.sqrt(mean_squared_error(y_train.iloc[-1260:], y_train_pred)))
print('Train mean_absolute_error         :', mean_absolute_error(y_train.iloc[-1260:], y_train_pred))

Train r-square                    : 0.0007114552003412156
Train mean_squared_error          : 0.0002134196329474943
Train roof of mean_squared_error  : 0.014608888833429265
Train mean_absolute_error         : 0.010644477253460023


In [68]:
# Test performance 
y_test_pred = pipe.predict(X_test)
print('Test r-square                    :', r2_score(y_test, y_test_pred))
print('Test mean_squared_error          :', mean_squared_error(y_test, y_test_pred))
print('Test roof of mean_squared_error  :', np.sqrt(mean_squared_error(y_test, y_test_pred)))
print('Test mean_absolute_error         :', mean_absolute_error(y_test, y_test_pred))

Test r-square                    : -0.020435722725925753
Test mean_squared_error          : 0.00015203367327041412
Test roof of mean_squared_error  : 0.012330193561757826
Test mean_absolute_error         : 0.00949644334126849


#### Naive predictor 

In [69]:
# Naive predictor should be average of y_train (random walk with drift)
# Use 1260 days of rtn 
y_dummy = pd.DataFrame(np.ones((len(y_test)))*y_train.iloc[-1260:].mean())
y_dummy

0
0   0.000657
1   0.000657
2   0.000657
3   0.000657
4   0.000657
5   0.000657
6   0.000657
7   0.000657
8   0.000657
9   0.000657
10  0.000657
11  0.000657
12  0.000657
13  0.000657
14  0.000657
15  0.000657
16  0.000657
17  0.000657
18  0.000657
19  0.000657
20  0.000657
21  0.000657
22  0.000657
23  0.000657
24  0.000657

In [70]:
# Naive performance 
print('Dummy r-square                    :', r2_score(y_test, y_dummy))
print('Dummy mean_squared_error          :', mean_squared_error(y_test, y_dummy))
print('Dummy roof of mean_squared_error  :', np.sqrt(mean_squared_error(y_test, y_dummy)))
print('Dummy mean_absolute_error         :', mean_absolute_error(y_test, y_dummy))

Dummy r-square                    : -0.021218528233832412
Dummy mean_squared_error          : 0.00015215030266134275
Dummy roof of mean_squared_error  : 0.012334922077635625
Dummy mean_absolute_error         : 0.009491508336628459


In [ ]:
Start from here
Start from here
Start from here

## 5.4) KNN

#### Explore KNN with make_pipeline()

In [276]:
pipe = make_pipeline(
    StandardScaler(), 
    KNeighborsRegressor(n_neighbors=5)
)

In [277]:
pipe.fit(X_train, y_train)

Pipeline(steps=[('standardscaler', StandardScaler()),
                ('kneighborsregressor', KNeighborsRegressor())])

In [278]:
pipe.score(X_train, y_train)

0.22716022965669558

In [279]:
pipe.score(X_test, y_test)

-0.2586259281959269

#### GridSearchCV with 1260 days training window (5 years), without month sine and cosine

In [283]:
n_neighbors = [int(n) for n in np.linspace(1, 20, num=20, endpoint=True)]
n_neighbors

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20]

In [284]:
pipe = make_pipeline(
    StandardScaler(), 
    KNeighborsRegressor()
)

In [285]:
param = {'kneighborsregressor__n_neighbors': n_neighbors}

gs = GridSearchCV(estimator = pipe,
                  param_grid = param,
                  cv = sliding_cv,
                  n_jobs = -1,
                  scoring = 'neg_mean_squared_error')
gs_fit = gs.fit(X_train, y_train)
pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
13       0.003989  6.304495e-04         0.002593    4.886172e-04   
12       0.004388  7.989057e-04         0.002194    7.460990e-04   
14       0.003590  4.884999e-04         0.002194    7.460217e-04   
11       0.004389  7.980113e-04         0.002792    3.995673e-04   
15       0.003590  7.979157e-04         0.001397    4.889282e-04   
16       0.003390  1.016597e-03         0.002394    4.888113e-04   
17       0.003192  3.992559e-04         0.001995    6.309774e-04   
10       0.003192  3.990174e-04         0.002195    7.466971e-04   
19       0.002991  5.519789e-07         0.001396    4.888891e-04   
18       0.003391  4.889281e-04         0.001795    3.993751e-04   
9        0.003591  7.970693e-04         0.001995    5.436780e-07   
8        0.003989  1.092232e-03         0.002394    4.891033e-04   
7        0.004188  7.462898e-04         0.002394    4.893175e-04   
5        0.004388  4.887731e-04         0.002195    3.990892e-04   
6        0.004389  7.971527e-04         0.002593    4.884222e-04   
4        0.004588  4.881884e-04         0.002793    7.469775e-04   
3        0.004588  4.885387e-04         0.002992    6.304495e-04   
2        0.003790  7.465320e-04         0.041290    4.731484e-02   
1        0.004388  7.970096e-04         0.102925    1.715778e-03   
0        0.004389  7.970097e-04         0.110304    2.053336e-03   

   param_kneighborsregressor__n_neighbors  \
13                                     14   
12                                     13   
14                                     15   
11                                     12   
15                                     16   
16                                     17   
17                                     18   
10                                     11   
19                                     20   
18                                     19   
9                                      10   
8                                       9   
7                                       8   
5                                       6   
6                                       7   
4                                       5   
3                                       4   
2                                       3   
1                                       2   
0                                       1   

                                      params  split0_test_score  \
13  {'kneighborsregressor__n_neighbors': 14}          -0.000101   
12  {'kneighborsregressor__n_neighbors': 13}          -0.000099   
14  {'kneighborsregressor__n_neighbors': 15}          -0.000100   
11  {'kneighborsregressor__n_neighbors': 12}          -0.000099   
15  {'kneighborsregressor__n_neighbors': 16}          -0.000104   
16  {'kneighborsregressor__n_neighbors': 17}          -0.000105   
17  {'kneighborsregressor__n_neighbors': 18}          -0.000110   
10  {'kneighborsregressor__n_neighbors': 11}          -0.000109   
19  {'kneighborsregressor__n_neighbors': 20}          -0.000109   
18  {'kneighborsregressor__n_neighbors': 19}          -0.000114   
9   {'kneighborsregressor__n_neighbors': 10}          -0.000114   
8    {'kneighborsregressor__n_neighbors': 9}          -0.000119   
7    {'kneighborsregressor__n_neighbors': 8}          -0.000122   
5    {'kneighborsregressor__n_neighbors': 6}          -0.000140   
6    {'kneighborsregressor__n_neighbors': 7}          -0.000138   
4    {'kneighborsregressor__n_neighbors': 5}          -0.000135   
3    {'kneighborsregressor__n_neighbors': 4}          -0.000158   
2    {'kneighborsregressor__n_neighbors': 3}          -0.000165   
1    {'kneighborsregressor__n_neighbors': 2}          -0.000155   
0    {'kneighborsregressor__n_neighbors': 1}          -0.000443   

    split1_test_score  split2_test_score  split3_test_score  \
13          -0.000287          -0.000122          -0.000171   
12          -0.000287          -0.000123          -0.000168   
14          -0.000288          -

In [286]:
# Take best parameters
gs_fit.best_params_

{'kneighborsregressor__n_neighbors': 14}

#### GridSearchCV with 1260 days training window (5 years), with month sine and cosine

We have updated X_train and X_test to include month sine and cosine

In [298]:
X_test.columns

Index(['ma50', 'rsi50', 'vol_1d_change', 'vol_1d_change_ma10', 'log_rtn_lag_0',
       'log_rtn_lag_1', 'log_rtn_lag_2', 'log_rtn_lag_3', 'log_rtn_lag_4',
       'log_rtn_lag_5', 'log_rtn_lag_6', 'log_rtn_lag_7', 'log_rtn_lag_8',
       'log_rtn_lag_9', 'log_rtn_lag_10', 'log_rtn_lag_11', 'log_rtn_lag_12',
       'log_rtn_lag_13', 'log_rtn_lag_14', '1d_future_month_sin',
       '1d_future_month_cos'],
      dtype='object')

In [299]:
pipe = make_pipeline(
    StandardScaler(), 
    KNeighborsRegressor()
)

In [300]:
n_neighbors = [int(n) for n in np.linspace(1, 20, num=20, endpoint=True)]
n_neighbors

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20]

In [301]:
param = {'kneighborsregressor__n_neighbors': n_neighbors}

gs = GridSearchCV(estimator = pipe,
                  param_grid = param,
                  cv = sliding_cv,
                  n_jobs = -1,
                  scoring = 'neg_mean_squared_error')
gs_fit = gs.fit(X_train, y_train)
pd.DataFrame(gs_fit.cv_results_).sort_values('mean_test_score', ascending=False)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
15       0.003790  7.461108e-04         0.002394    4.883832e-04   
16       0.004987  6.143617e-07         0.002992    7.776979e-07   
14       0.003391  4.888311e-04         0.001796    7.464549e-04   
17       0.005187  3.991850e-04         0.002793    3.989956e-04   
13       0.003790  9.768051e-04         0.002194    3.993278e-04   
18       0.004787  3.990651e-04         0.002593    4.880343e-04   
19       0.004786  7.465953e-04         0.002221    4.205422e-04   
12       0.002992  5.642013e-07         0.001795    3.986362e-04   
11       0.003590  4.888715e-04         0.001396    4.885975e-04   
10       0.003392  7.978202e-04         0.001995    2.132481e-07   
6        0.003989  6.302989e-04         0.002194    7.466973e-04   
9        0.003391  4.885000e-04         0.001795    7.464423e-04   
8        0.004388  4.887918e-04         0.001994    6.309018e-04   
7        0.004588  4.882274e-04         0.002593    4.888703e-04   
5        0.004388  4.887724e-04         0.002594    4.889282e-04   
4        0.003591  4.879751e-04         0.002393    4.882467e-04   
3        0.003790  7.461236e-04         0.002194    3.991370e-04   
2        0.002793  2.309018e-03         0.110410    1.319665e-01   
1        0.000000  0.000000e+00         0.275159    6.250477e-03   
0        0.000000  0.000000e+00         0.272034    0.000000e+00   

   param_kneighborsregressor__n_neighbors  \
15                                     16   
16                                     17   
14                                     15   
17                                     18   
13                                     14   
18                                     19   
19                                     20   
12                                     13   
11                                     12   
10                                     11   
6                                       7   
9                                      10   
8                                       9   
7                                       8   
5                                       6   
4                                       5   
3                                       4   
2                                       3   
1                                       2   
0                                       1   

                                      params  split0_test_score  \
15  {'kneighborsregressor__n_neighbors': 16}          -0.000080   
16  {'kneighborsregressor__n_neighbors': 17}          -0.000080   
14  {'kneighborsregressor__n_neighbors': 15}          -0.000083   
17  {'kneighborsregressor__n_neighbors': 18}          -0.000084   
13  {'kneighborsregressor__n_neighbors': 14}          -0.000086   
18  {'kneighborsregressor__n_neighbors': 19}          -0.000088   
19  {'kneighborsregressor__n_neighbors': 20}          -0.000086   
12  {'kneighborsregressor__n_neighbors': 13}          -0.000097   
11  {'kneighborsregressor__n_neighbors': 12}          -0.000101   
10  {'kneighborsregressor__n_neighbors': 11}          -0.000103   
6    {'kneighborsregressor__n_neighbors': 7}          -0.000117   
9   {'kneighborsregressor__n_neighbors': 10}          -0.000113   
8    {'kneighborsregressor__n_neighbors': 9}          -0.000106   
7    {'kneighborsregressor__n_neighbors': 8}          -0.000119   
5    {'kneighborsregressor__n_neighbors': 6}          -0.000130   
4    {'kneighborsregressor__n_neighbors': 5}          -0.000176   
3    {'kneighborsregressor__n_neighbors': 4}          -0.000188   
2    {'kneighborsregressor__n_neighbors': 3}          -0.000172   
1    {'kneighborsregressor__n_neighbors': 2}          -0.000207   
0    {'kneighborsregressor__n_neighbors': 1}          -0.000384   

    split1_test_score  split2_test_score  split3_test_score  \
15          -0.000233          -0.000122          -0.000188   
16          -0.000233          -0.000125          -0.000189   
14          -0.000238          -

## 5.5) ARIMA

#### Explore TimeSeriesSplit()

In [14]:
# Take timeseries 2012-2017
ts = zion_1.loc["2012":"2017", "log_rtn"].copy()

In [15]:
type(ts)

pandas.core.series.Series

In [16]:
ts.shape

(1508,)

In [21]:
# Try test_size = 1
sliding_cv = TimeSeriesSplit(n_splits=125, test_size=1, max_train_size=1260)

for fold, (main_ind, valid_ind) in enumerate(sliding_cv.split(ts)):
    print(f"Fold {fold} ----")
    print(f"Train indices: {main_ind}")
    print(f"Valid indices: {valid_ind}")

Fold 0 ----
Train indices: [ 123  124  125 ... 1380 1381 1382]
Valid indices: [1383]
Fold 1 ----
Train indices: [ 124  125  126 ... 1381 1382 1383]
Valid indices: [1384]
Fold 2 ----
Train indices: [ 125  126  127 ... 1382 1383 1384]
Valid indices: [1385]
Fold 3 ----
Train indices: [ 126  127  128 ... 1383 1384 1385]
Valid indices: [1386]
Fold 4 ----
Train indices: [ 127  128  129 ... 1384 1385 1386]
Valid indices: [1387]
Fold 5 ----
Train indices: [ 128  129  130 ... 1385 1386 1387]
Valid indices: [1388]
Fold 6 ----
Train indices: [ 129  130  131 ... 1386 1387 1388]
Valid indices: [1389]
Fold 7 ----
Train indices: [ 130  131  132 ... 1387 1388 1389]
Valid indices: [1390]
Fold 8 ----
Train indices: [ 131  132  133 ... 1388 1389 1390]
Valid indices: [1391]
Fold 9 ----
Train indices: [ 132  133  134 ... 1389 1390 1391]
Valid indices: [1392]
Fold 10 ----
Train indices: [ 133  134  135 ... 1390 1391 1392]
Valid indices: [1393]
Fold 11 ----
Train indices: [ 134  135  136 ... 1391 1392 1393]


In [57]:
# For Fold 124 - fit, forecast and calculate mse
# .iloc() second index are exclusive
mod = ARIMA(ts.iloc[247:1507], order=(1,0,1))
res = mod.fit()

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)


In [58]:
# forecast() output just the forecast number
pred = res.forecast(1)

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(


In [59]:
type(pred)

pandas.core.series.Series

In [60]:
pred

1260    0.001158
dtype: float64

In [62]:
# The index of the prediction is [1260], not [0]
pred[1260]

0.0011575509633286007

In [63]:
# look at index of residual
res.resid

Date
2012-12-27   -0.000254
2012-12-28   -0.006850
2012-12-31    0.012193
2013-01-02    0.025925
2013-01-03    0.000120
                ...   
2017-12-21    0.013448
2017-12-22   -0.003632
2017-12-26   -0.009561
2017-12-27   -0.003589
2017-12-28    0.011686
Length: 1260, dtype: float64

In [29]:
# get_forecast() output result wrapper include at least standard error
pred_other = res.get_forecast(steps=1)

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(


In [30]:
type(pred_other)

statsmodels.tsa.statespace.mlemodel.PredictionResultsWrapper

In [32]:
pred_other.predicted_mean

1260    0.001158
dtype: float64

In [33]:
ts.iloc[1507]

-0.0099834439841832

In [35]:
type(ts.iloc[1507])

numpy.float64

In [39]:
# Caclutate erro
(ts.iloc[1507] - pred)

1260   -0.011141
dtype: float64

In [38]:
# Caclutate mse
(ts.iloc[1507] - pred)**2

1260    0.000124
dtype: float64

In [42]:
# Calculate mse with TimeSeriesSplit()
sliding_cv = TimeSeriesSplit(n_splits=125, test_size=1, max_train_size=1260)

for fold, (main_ind, valid_ind) in enumerate(sliding_cv.split(ts)):
    if fold == 124:
        train = ts[main_ind] # main_ind here is list of indexes. So this includes both beg and end
        test = ts[valid_ind]
        mod = ARIMA(train, order=(1,0,1))
        res = mod.fit()
        pred = res.forecast(1)
        mse = mean_squared_error(test, pred)
        print(mse)

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)


0.00012412176842048348


C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(


Yes the mse is the same whether calculate manually or use TimeSeriesSplit()

In [50]:
# Loop over all 125 fold
sliding_cv = TimeSeriesSplit(n_splits=125, test_size=1, max_train_size=1260)

mses = []

for fold, (main_ind, valid_ind) in enumerate(sliding_cv.split(ts)):
    if fold < 30:
        train = ts[main_ind] # main_ind here is list of indexes. So this includes both beg and end
        test = ts[valid_ind]
        mod = ARIMA(train, order=(1,0,1))
        res = mod.fit()
        pred = res.forecast(1)
        mse = mean_squared_error(test, pred)
        mses.append(mse)

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

In [51]:
mses

[0.00032251771088792104,
 9.93151336507243e-07,
 0.0002013826581589509,
 4.4067716100799965e-05,
 8.842336101898397e-06,
 0.00012975775862883083,
 0.00010254415804519252,
 2.0849472190636577e-05,
 5.955883450011871e-05,
 7.10450744668616e-05,
 5.7238021301905135e-05,
 5.0351631012368876e-06,
 1.9609007609522023e-05,
 3.465520524684622e-05,
 0.00022722620907299074,
 5.665480107059076e-05,
 0.00047552887009535174,
 0.00016856614490426717,
 3.2813694820909532e-06,
 2.180435400981359e-06,
 1.6529418019648162e-07,
 6.240382430546397e-05,
 5.036903533361947e-05,
 0.0001851847422038849,
 9.039682321390287e-05,
 1.0226465366030925e-06,
 0.00018094361925101156,
 0.00034547109651556044,
 9.11044069106702e-05,
 0.00041319517553856767]

In [52]:
len(mses)

30

In [53]:
len(mses[0:25]) # Does not include the last index

25

In [54]:
mses[0:25]

[0.00032251771088792104,
 9.93151336507243e-07,
 0.0002013826581589509,
 4.4067716100799965e-05,
 8.842336101898397e-06,
 0.00012975775862883083,
 0.00010254415804519252,
 2.0849472190636577e-05,
 5.955883450011871e-05,
 7.10450744668616e-05,
 5.7238021301905135e-05,
 5.0351631012368876e-06,
 1.9609007609522023e-05,
 3.465520524684622e-05,
 0.00022722620907299074,
 5.665480107059076e-05,
 0.00047552887009535174,
 0.00016856614490426717,
 3.2813694820909532e-06,
 2.180435400981359e-06,
 1.6529418019648162e-07,
 6.240382430546397e-05,
 5.036903533361947e-05,
 0.0001851847422038849,
 9.039682321390287e-05]

In [55]:
mses[25:50]

[1.0226465366030925e-06,
 0.00018094361925101156,
 0.00034547109651556044,
 9.11044069106702e-05,
 0.00041319517553856767]

In [56]:
# Calculate mse of the first 25
sum(mses[0:25])/len(mses[0:25])

9.600215267762275e-05

In [67]:
# The code above use mean_squared_error() in every loop. It is better to save pred in a list and use 
# mean_squared_error(test, pred) only one time
# Loop over all 125 fold
sliding_cv = TimeSeriesSplit(n_splits=125, test_size=1, max_train_size=1260)

ts_hat = []
ts_test = []

for fold, (main_ind, valid_ind) in enumerate(sliding_cv.split(ts)):
    train = ts[main_ind] # main_ind here is list of indexes. So this includes both beg and end
    test = ts[valid_ind]
    mod = ARIMA(train, order=(1,0,1))
    res = mod.fit()
    pred = res.forecast()
    ts_hat.append(pred)
    ts_test.append(test)
    
# The warning is OK. We don't use our date index in forecasting. Our data is in trading day, not calendar day. 
# Using date index and frequence, might lead to forecasting return for weekend.
# Because of no frequency, the index of forecast(1) is [1260] instead of [0]

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\sit

...

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\sit

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

In [68]:
print(len(ts_hat))
print(len(ts_test))

125
125


In [69]:
# Calculate mse for the first cross-validation fold.
mean_squared_error(ts_test[0:25], ts_hat[0:25])
# Yes, we have the same mse as the code before

9.600215267762275e-05

In [70]:
# But we don't have to calculate mse for each folds. We just take mse of all 5 fold
mean_squared_error(ts_test, ts_hat)
# Yes this number is comparable with other methods (Random Forest, KNN)

0.0001771906809508891

In [71]:
print(mean_squared_error(ts_test[0:25], ts_hat[0:25]))
print(mean_squared_error(ts_test[25:50], ts_hat[25:50]))
print(mean_squared_error(ts_test[50:75], ts_hat[50:75]))
print(mean_squared_error(ts_test[75:100], ts_hat[75:100]))
print(mean_squared_error(ts_test[100:125], ts_hat[100:125]))

9.600215267762275e-05
0.0002542019484662529
0.00010357425992754937
0.00019794100611789122
0.00023423403756512925


#### Choosing best ARIMA model
Our return series is stationary so we will not need to difference. We will consider autoregression order range of 0 to 4; and moving average order range of 0 to 4. 

Function to evaluate an arima model

In [74]:
def evaluate_arima_model(ts, arima_order):
    sliding_cv = TimeSeriesSplit(n_splits=125, test_size=1, max_train_size=1260)

    ts_hat = []
    ts_test = []

    for fold, (main_ind, valid_ind) in enumerate(sliding_cv.split(ts)):
        train = ts[main_ind] # main_ind here is list of indexes. So this includes both beg and end
        test = ts[valid_ind]
        mod = ARIMA(train, order=arima_order)
        res = mod.fit()
        pred = res.forecast()
        ts_hat.append(pred)
        ts_test.append(test)
    return mean_squared_error(ts_test, ts_hat)

In [75]:
# Test with order (1, 0, 1)
evaluate_arima_model(ts, arima_order=(1, 0, 1))
# Yes, we have the same result

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

...

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

0.0001771906809508891

Loop over the potential arima_order

In [84]:
param_list = [(p, d, q) for p in range(5) for d in range(1) for q in range (5)]

mses = []
arima_orders = []

for order in param_list:
    arima_orders.append(order)
    mses.append(evaluate_arima_model(ts, arima_order=order))    

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

...

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\sit

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

In [85]:
results = pd.DataFrame(list(zip(arima_orders, mses)), columns = ['arima_order', 'mse'])
results

arima_order       mse
0    (0, 0, 0)  0.000175
1    (0, 0, 1)  0.000174
2    (0, 0, 2)  0.000173
3    (0, 0, 3)  0.000175
4    (0, 0, 4)  0.000176
5    (1, 0, 0)  0.000174
6    (1, 0, 1)  0.000177
7    (1, 0, 2)  0.000174
8    (1, 0, 3)  0.000175
9    (1, 0, 4)  0.000176
10   (2, 0, 0)  0.000173
11   (2, 0, 1)  0.000175
12   (2, 0, 2)  0.000174
13   (2, 0, 3)  0.000175
14   (2, 0, 4)  0.000175
15   (3, 0, 0)  0.000174
16   (3, 0, 1)  0.000174
17   (3, 0, 2)  0.000175
18   (3, 0, 3)  0.000174
19   (3, 0, 4)  0.000175
20   (4, 0, 0)  0.000175
21   (4, 0, 1)  0.000175
22   (4, 0, 2)  0.000176
23   (4, 0, 3)  0.000176
24   (4, 0, 4)  0.000174

In [86]:
results.sort_values(by=['mse'])

arima_order       mse
10   (2, 0, 0)  0.000173
2    (0, 0, 2)  0.000173
24   (4, 0, 4)  0.000174
1    (0, 0, 1)  0.000174
7    (1, 0, 2)  0.000174
5    (1, 0, 0)  0.000174
12   (2, 0, 2)  0.000174
15   (3, 0, 0)  0.000174
16   (3, 0, 1)  0.000174
18   (3, 0, 3)  0.000174
11   (2, 0, 1)  0.000175
17   (3, 0, 2)  0.000175
3    (0, 0, 3)  0.000175
8    (1, 0, 3)  0.000175
13   (2, 0, 3)  0.000175
19   (3, 0, 4)  0.000175
0    (0, 0, 0)  0.000175
14   (2, 0, 4)  0.000175
20   (4, 0, 0)  0.000175
21   (4, 0, 1)  0.000175
4    (0, 0, 4)  0.000176
9    (1, 0, 4)  0.000176
22   (4, 0, 2)  0.000176
23   (4, 0, 3)  0.000176
6    (1, 0, 1)  0.000177

In [89]:
# Save results to hard disk
# Save to csv
results.to_csv('../data/zion_arima_0_difference.csv')
# Made this file read-only

Loop over possible arima_order. Now with first difference

In [88]:
start = time.time()

param_list = [(p, d, q) for p in range(5) for d in range(1,2) for q in range (5)]

mses = []
arima_orders = []

for order in param_list:
    arima_orders.append(order)
    mses.append(evaluate_arima_model(ts, arima_order=order))
    
end = time.time()
run_time = (end - start)
print(run_time)

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\nguye\a

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\sit

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\sit

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\U

...

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\sit

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\sit

C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:471: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  self._init_dates(dates, freq)
C:\Users\nguye\anaconda3\lib\sit

3695.5724527835846


C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\base\model.py:604: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "
C:\Users\nguye\anaconda3\lib\site-packages\statsmodels\tsa\base\tsa_model.py:834: ValueWarning: No supported index is available. Prediction results will be given with an integer index beginning at `start`.
  return get_prediction_index(


In [92]:
results = pd.DataFrame(list(zip(arima_orders, mses)), columns = ['arima_order', 'mse'])
results

arima_order       mse
0    (0, 1, 0)  0.000311
1    (0, 1, 1)  0.000175
2    (0, 1, 2)  0.000174
3    (0, 1, 3)  0.000173
4    (0, 1, 4)  0.000174
5    (1, 1, 0)  0.000268
6    (1, 1, 1)  0.000174
7    (1, 1, 2)  0.000180
8    (1, 1, 3)  0.000176
9    (1, 1, 4)  0.000174
10   (2, 1, 0)  0.000256
11   (2, 1, 1)  0.000173
12   (2, 1, 2)  0.000178
13   (2, 1, 3)  0.000176
14   (2, 1, 4)  0.000175
15   (3, 1, 0)  0.000230
16   (3, 1, 1)  0.000175
17   (3, 1, 2)  0.000173
18   (3, 1, 3)  0.000175
19   (3, 1, 4)  0.000173
20   (4, 1, 0)  0.000218
21   (4, 1, 1)  0.000176
22   (4, 1, 2)  0.000178
23   (4, 1, 3)  0.000172
24   (4, 1, 4)  0.000175

In [93]:
results.sort_values(by=['mse'])

arima_order       mse
23   (4, 1, 3)  0.000172
3    (0, 1, 3)  0.000173
11   (2, 1, 1)  0.000173
17   (3, 1, 2)  0.000173
19   (3, 1, 4)  0.000173
9    (1, 1, 4)  0.000174
2    (0, 1, 2)  0.000174
6    (1, 1, 1)  0.000174
4    (0, 1, 4)  0.000174
1    (0, 1, 1)  0.000175
18   (3, 1, 3)  0.000175
24   (4, 1, 4)  0.000175
14   (2, 1, 4)  0.000175
16   (3, 1, 1)  0.000175
8    (1, 1, 3)  0.000176
13   (2, 1, 3)  0.000176
21   (4, 1, 1)  0.000176
12   (2, 1, 2)  0.000178
22   (4, 1, 2)  0.000178
7    (1, 1, 2)  0.000180
20   (4, 1, 0)  0.000218
15   (3, 1, 0)  0.000230
10   (2, 1, 0)  0.000256
5    (1, 1, 0)  0.000268
0    (0, 1, 0)  0.000311

In [94]:
# Save results to hard disk
# Save to csv
results.to_csv('../data/zion_arima_1_difference.csv')
# Made this file read-only